This Jupyter notebook provides a step-by-step guide for uploading and managing geospatial data in the Geovio platform. It demonstrates how to extract example data, create and upload an Area of Interest (AOI), import features, check AOI processing status, retrieve platform and band information, and upload a mosaic for further analysis. The notebook is designed as a practical introduction to the basic data workflow in Geovio, making it easier to get started with remote sensing and geospatial analysis.

&nbsp;
&nbsp;

**Files for download:**  
- **Entrypoint file:** [Download Jupyter Notebook `base.ipynb`](base.ipynb)  
- **Datazip file:** [Download `base_datazip.zip`](/docs/example_data/base_datazip.zip)  

**Video walkthrough:**  

<video width="600" controls>
  <source src="/docs/videos/base.mp4" type="video/mp4">
  Your browser does not support HTML video.
</video>


## Import libraries

In [ ]:
import os
import zipfile
import requests
import json
import time

from datetime import date

## Authorization

Before making API requests, we need to include an authorization header.  
This header ensures that the server can verify our identity and grant us access to the requested resources.  

In [ ]:
access_token = os.getenv("JWT_TOKEN")
geovio_api_url = os.getenv("GEOVIO_API_URL")
transfer_api_url = os.getenv("TRANSFER_API_URL")
workspace_id = os.getenv("WORKSPACE")

# Validate inputs
if not access_token:
    raise ValueError("JWT_TOKEN environment variable is not set")

if not geovio_api_url:
    raise ValueError("GEOVIO_API_URL environment variable is not set")

if not transfer_api_url:
    raise ValueError("TRANSFER_API_URL environment variable is not set")

if not workspace_id:
    raise ValueError("WORKSPACE environment variable is not set")

headers = {
    "accept": "application/json",
    "Authorization": f"Bearer {access_token}"
}

## Extract example from Datazip File

In [ ]:
with zipfile.ZipFile("/workdir/base_datazip.zip", 'r') as zip_ref:
    zip_ref.extractall("/workdir")

aoi_filename: str = "aoi.geojson"
mosaic_filename: str = "mosaic.tif"
aoi_path: str = f"/workdir/example_data/{aoi_filename}"
mosaic_path: str = f"/workdir/example_data/{mosaic_filename}"

if not os.path.exists(aoi_path):
    raise FileNotFoundError("AoI file was not extracted corectly")

if not os.path.exists(mosaic_path):
    raise FileNotFoundError("Mosaic file was not extracted corectly")

## Upload AOI

An **Area of Interest (AOI)** defines the spatial extent used in further processing.  
Each AOI must be linked to an existing workspace.

- Provide AOI metadata (`title`, `description`) and the target `workspace_id`.  
- The geometry can be supplied in `areaOfInterestGeoJSON` as valid `FeatureCollection`.  
- A `POST` request to `/AreaInterest` creates the AOI and returns its numeric `aoi_id`.  


In [ ]:
create_aoi_url: str = f"{geovio_api_url}/AreaInterest"

create_payload = {
    "title": "Example aoi",
    "description": "Example aoi",
    "workspace": workspace_id,
    "areaOfInterestGeoJSON": None
}

create_aoi_response = requests.post(create_aoi_url, json=create_payload, headers=headers)
aoi_id: int = int(create_aoi_response.text)

## Import Features  

Geometries can be uploaded into an existing AOI created earlier.  

- The target AOI is referenced by its `aoi_id`.  
- Supported input is a GeoJSON file containing the geometries.  
- Optional parameters (e.g., `simplifyMode`) can be specified to control preprocessing.  
- A `POST` request to `/AreaInterest/{aoi_id}/import` uploads the file.  
- On success, the AOI is populated with the provided features.  


In [ ]:
upload_aoi_url: str = f"{geovio_api_url}/AreaInterest/{aoi_id}/import"

params = {
    "simplifyMode": 1
}

files = [
    ("files", (aoi_filename, open(aoi_path, "rb")))
]

upload_aoi_response = requests.post(upload_aoi_url, headers=headers, files=files)

if upload_aoi_response.status_code != 200:
    print(upload_aoi_response.text)

## Check AOI  

After uploading, the AOI needs to be processed by the server.  

- The status of the AOI can be retrieved via `/AreaInterest/{aoi_id}`.  
- Poll the endpoint until `statusParent` indicates that processing is complete (`1`).  
- Once completed, the AOI is ready for further operations such as mosaic creation or analysis.  


In [ ]:
aoi_status_url: str = f"{geovio_api_url}/AreaInterest/{aoi_id}"

parentStatus: int = 0

while parentStatus != 1:
    aoi_status_response = requests.get(aoi_status_url, headers=headers)
    
    aoi_path: dict = aoi_status_response.json()
    parentStatus: int = aoi_path["statusParent"]
    
    print("check aoi upload")
    time.sleep(10)

print("aoi uploaded successfully")

## Get Platform Details  

Retrieve platform information to select the appropriate dataset for your input TIFF file.

In [ ]:
platform_list_response = requests.get(f"{geovio_api_url}/IndexLibrary/platform", headers=headers)

platform_list: dict = platform_list_response.json()
platform: dict = [i for i in platform_list if i["valueId"] == "sentinel-2_msi"][0]
platform_id: int = platform["id"]
platform_valueId: str = platform["valueId"]

platform_resolution_response = requests.get(f"{geovio_api_url}/Metadata/resolution/{platform_valueId}",headers=headers)
platform_resolution: dict = platform_resolution_response.json()
resolution_id: int = [i["id"] for i in platform_resolution if i["resolution"] == 10]

## Get Platform Band Resolution  

Retrieve the spectral band details for the selected platform.  

In [ ]:
platform_band_response = requests.get(f"{geovio_api_url}/Metadata/band?Platform={platform_valueId}", headers=headers)
platform_band_list = platform_band_response.json()
platform_bands = [{"id": i["id"], "files": [mosaic_filename]} for i in platform_band_list]

## Import Mosaic  

Upload a mosaic file to an existing AOI.  
If no AOI exists, one will be created automatically during processing.  

- Define mosaic metadata (`title`, `description`, `date range`, `resolution`, `platform`, `workspace`, `AOI`).  
- Prepare the mosaic file and associated settings (e.g., band mapping) as multipart form data.  
- Send a `POST` request to `/Mosaic/upload` to start the upload.  
- On success, the mosaic is linked to the AOI and ready for analysis.  


In [ ]:
upload_mosaic_url = f"{transfer_api_url}/Mosaic/upload"

today = date.today()
formatted = today.strftime("%Y-%m-%d")  

params = {
    "title": "Sentinel 2",
    "description": "Uploaded mosaic from jupyter",
    "fromDate": formatted,
    "toDate": formatted,
    "resolution": resolution_id,
    "platform": platform_id,
    "workspace": workspace_id,
    "aoi": aoi_id,
    "clipAois": "[]"
}

multipart_files = [
    ("files", (mosaic_filename, open(mosaic_path, "rb"), "image/tiff"))
]

settings = {
    "bands": platform_bands
}

multipart_files.append(("settings", (None, json.dumps(settings), "application/json")))

print("Mosaic upload started")

mosaic_upload_response = requests.post(
    upload_mosaic_url,
    params=params,
    headers=headers,
    files=multipart_files
)

if mosaic_upload_response.status_code == 200:
    print("Mosai upload was sussessfull")
else:
    print(mosaic_upload_response.text)